In [21]:
#Load libraries
import http.client
import requests
import json
import pandas as pd
import csv
import numpy as np
import altair as alt
from altair import datum
from google.colab import drive, files # specific to Google Colab
import time
import re


# show all columns
pd.set_option('display.max_columns', None)

In [2]:
detail_cols = ['streetAddress',
 'city',
 'county',
 'zipcode',
 'state',
 'longitude',
 'latitude',
 'price',
 'homeType',
 'homeStatus',
 'description',
 'datePosted',
 'timeOnZillow',
 'zestimate',
 'rentZestimate',
 'livingArea',
 'bedrooms',
 'bathrooms',
 'yearBuilt',
 'description',
 'priceHistory',
 'taxHistory',
 'propertyTypeDimension',
 'annualHomeownersInsurance',
 'pageViewCount',
 'zpid',
 'resoFacts.cityRegion',
 'resoFacts.view',
 'resoFacts.waterViewYN',
 'resoFacts.isNewConstruction',
 'resoFacts.pricePerSquareFoot',
 'resoFacts.hasGarage',
 'resoFacts.garageSpaces',
 'resoFacts.lotSize',
 'resoFacts.associationFee',
 'resoFacts.hasPetsAllowed',
 'resoFacts.elementarySchool',
 'resoFacts.canRaiseHorses',
 'resoFacts.middleOrJuniorSchool',
 'resoFacts.highSchool'
 ]

In [4]:
##df_fl_prop = pd.read_csv("fl_houses_detail_1.csv",header = None, delimiter="\t", quoting=csv.QUOTE_NONE, encoding='utf-8')
df_fl_prop = pd.read_csv("consolidated_fl.csv", usecols=detail_cols)

In [5]:
brush = alt.selection_interval()
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [6]:
df_hometime = df_fl_prop[['city','zipcode','datePosted','timeOnZillow']]

In [11]:
df_hometime.dtypes

city            object
zipcode         object
datePosted      object
timeOnZillow    object
dtype: object

In [10]:
df_hometime['zipcode'] = df_hometime['zipcode'].astype(str)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [12]:
df_hometime.head()

city  zipcode  datePosted timeOnZillow
0  Alachua  32615.0  2022-03-04     108 days
1  Alachua  32615.0  2022-06-09      11 days
2  Alachua  32615.0  2022-06-15       5 days
3  Alachua  32615.0  2022-02-09     132 days
4  Alachua  32615.0  2022-03-27      86 days

In [13]:
df_hometime['datePosted'] = pd.to_datetime(df_hometime['datePosted'])

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [15]:
df_hometime.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 34302 entries, 0 to 34301
Data columns (total 4 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   city          34302 non-null  object        
 1   zipcode       34302 non-null  object        
 2   datePosted    34181 non-null  datetime64[ns]
 3   timeOnZillow  34277 non-null  object        
dtypes: datetime64[ns](1), object(3)
memory usage: 1.0+ MB


In [16]:
df_hometime.head()

city  zipcode datePosted timeOnZillow
0  Alachua  32615.0 2022-03-04     108 days
1  Alachua  32615.0 2022-06-09      11 days
2  Alachua  32615.0 2022-06-15       5 days
3  Alachua  32615.0 2022-02-09     132 days
4  Alachua  32615.0 2022-03-27      86 days

In [17]:
df_hometime['zipcode'] = df_hometime['zipcode'] .str[:-2]

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [18]:
df_hometime.head()

city zipcode datePosted timeOnZillow
0  Alachua   32615 2022-03-04     108 days
1  Alachua   32615 2022-06-09      11 days
2  Alachua   32615 2022-06-15       5 days
3  Alachua   32615 2022-02-09     132 days
4  Alachua   32615 2022-03-27      86 days

In [34]:
curr_time = pd.to_datetime("now")

In [35]:
df_hometime['days_listed'] = df_hometime['datePosted'] - curr_time

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [36]:
df_hometime.head()

city zipcode datePosted timeOnZillow                days_listed
0  Alachua   32615 2022-03-04     108 days -138 days +23:27:22.031311
1  Alachua   32615 2022-06-09      11 days  -41 days +23:27:22.031311
2  Alachua   32615 2022-06-15       5 days  -35 days +23:27:22.031311
3  Alachua   32615 2022-02-09     132 days -161 days +23:27:22.031311
4  Alachua   32615 2022-03-27      86 days -115 days +23:27:22.031311

In [42]:
df_hometime['days_listed'] = df_hometime['days_listed'].dt.days

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [44]:
df_hometime['days_listed'] = abs(df_hometime['days_listed'])

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [50]:
df_hometime['days_listed'] =  df_hometime['days_listed'].astype(float)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [51]:
df_hometime.head()

city zipcode datePosted timeOnZillow  days_listed
0  Alachua   32615 2022-03-04     108 days        138.0
1  Alachua   32615 2022-06-09      11 days         41.0
2  Alachua   32615 2022-06-15       5 days         35.0
3  Alachua   32615 2022-02-09     132 days        161.0
4  Alachua   32615 2022-03-27      86 days        115.0

In [ ]:
df3 = df_hometime.groupby()

In [46]:
agg_func_math = {
    'days_listed':
    ['sum', 'mean', 'median', 'min', 'max', 'std', 'var', 'mad', 'prod']
}

In [48]:
df_hometime.groupby(['zipcode']).agg(agg_func_math)

days_listed                                                            \
                sum        mean median   min    max         std           var   
zipcode                                                                         
32003        2620.0   74.857143   53.0  31.0  333.0   58.493913   3421.537815   
32008        1150.0  104.545455  105.0  47.0  231.0   51.686291   2671.472727   
32009         754.0  150.800000   76.0  54.0  337.0  126.181219  15921.700000   
32011        2276.0   78.482759   41.0  30.0  408.0   87.473515   7651.615764   
32024        3236.0   82.974359   68.0  33.0  316.0   58.337262   3403.236167   
...             ...         ...    ...   ...    ...         ...           ...   
34990        6457.0   70.184783   54.5  29.0  232.0   39.932341   1594.591854   
34994        2417.0   86.321429   75.0  33.0  238.0   50.803218   2580.966931   
34996        2079.0   83.160000   65.0  33.0  380.0   68.781466   4730.890000   
34997        2773.0   77.027778   70.0  34.0  145.0   28.932914    837.113492   
36442         813.0  203.250000  245.0  50.0  273.0  103.015775  10612.250000   

                                    
                mad           prod  
zipcode                             
32003     38.612245   6.301381e+62  
32008     36.495868   5.361697e+21  
32009    104.960000   1.883711e+10  
32011     51.871581   1.392890e+51  
32024     40.477318   7.892605e+71  
...             ...            ...  
34990     30.215265  7.261935e+164  
34994     37.010204   3.164125e+52  
34996     37.056000   1.468248e+46  
34997     24.143519   7.052025e+66  
36442     76.625000   8.193412e+08  

[922 rows x 9 columns]

In [99]:
brush = alt.selection(type='interval')

points = alt.Chart(df_hometime).mark_point().encode(
    x=alt.X(
        "zipcode:N",
        axis=alt.Axis(title="Zipcodes in Florida")
    ),
    y=alt.Y(
        "mean_days_listed:Q",
        title="Average Days Listed on Zillow",
        scale=alt.Scale(zero=False)
    ),
    color=alt.condition(brush, 'zipcode:N', alt.value('lightgray'))
).add_selection(
    brush
).transform_aggregate(
    mean_days_listed='mean(days_listed)',
    groupby=["zipcode"]
).interactive()
points

alt.Chart(...)

In [ ]:
df_hometime['city'] = df_hometime['city'].str.upper()

In [ ]:
df_hometime.sort_values(by='city', ascending=False)

In [67]:
df_hometime2 = df_hometime[['city','zipcode','days_listed']]

In [ ]:
df_hometime2.head()

In [ ]:
df_hometime2.groupby(['zipcode']).head()

In [ ]:
df_hometime2.groupby(['zipcode']).agg(agg_func_math)